# Create input for regressions

This notebook creates pivoted tables to be used as input for the regressions. Creates one table with the values per gene per sample, one with the total per gene and one with the total per sample. It parses several deepCSA methods:

- Mutation density (NA are fill with zeros in deepCSA)
- OncodriveFML (NA fill with zeros when subsetting by significance, but only non-significant values. Need to change this part of the function to provide one table like this and another with NA, for the heatmaps)
- Omega (as in OncodriveFML)
- Mutated genomes

In [ ]:
import pandas as pd
import os

In [ ]:
pd.set_option('display.max_columns', None)

In [ ]:
# paths
cluster_dir = "/data/bbg/"
deepcsa_run_dir = "path/to/your/run" # change

mutdensity_file = os.path.join(deepcsa_run_dir, "mutdensity/all_mutdensities.tsv")
oncodrivefml_dir = os.path.join(deepcsa_run_dir, "oncodrivefmlsnvs")
omega_dir = os.path.join(deepcsa_run_dir, "omegagloballoc") 


In [ ]:
# metadata
panel = ['KMT2D','ARID1A','KDM6A','RBM10', "etc"] # define your panel
samples = ["01_BDO", "02_BDO", "etc"] # define your samples

# you can also load this information from a metadata file or where you have it stored

In [15]:
def create_metric_table(metric_df, metric_var, rows_var, cols_var,
                        rows_names, cols_names, 
                        total_cols_by, total_rows_by,
                        metric_var4file, save_files_dir,
                        keep_rows_ordered = True, keep_cols_ordered = True):
    """
    Converts metric_df in a pivoted table using 
    metric_var, rows_var and cols_var. Saves this 
    dataframe with columns as cols_names and
    index as rows_names, regardless of any of the 
    provided names is not in metric_df (thus, that
    column/row is filled with NA). Orders rows and/or
    columns if indicated according to cols_names/rows_names
    order. Also, saces two dataframes with the totals
    of the rows and the columns, according to total_by_cols
    and total_by_rows. Keeps as well all cols_names and rows_names
    
    Parameters
    ----------
    metric_df: pandas Dataframe
        Initial dataframe with at least 3 columns named
        as provided in metric_var, rows_var, cols_var
    metric_var: str
        Column name for the values to be used to fill 
        the pivoted dataframe
    rows_var: str
        Column name for the values to be used as row names
        of the pivoted dataframe
    cols_var: str
        Column name for the values to be used as column names
        of the pivoted dataframe
    rows_names: list
        List of values to be used as the row names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add rows with NA we want to keep for downstream 
        analysis
    cols_names: list
        List of values to be used as the column names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add columns with NA we want to keep for downstream 
        analysis
    total_cols_by: str
        How to calculate the total for the columns of the dataframe.
        If "sum", "mean" or "median", calculates the total from the 
        main pivoted dataframe. If other value, the total is provided
        in metric_df and total_cols_by value should correspond with the 
        value used in the specific metric_df to gather all the columns
        into one value.
    total_rows_by: str
        How to calculate the total for the rows of the dataframe.
        If "sum", "mean" or "median", calculates the total from the 
        main pivoted dataframe. If other value, the total is provided
        in metric_df and total_rows_by value should correspond with the 
        value used in the specific metric_df to gather all the rows
    metric_var4file: str
        Name to be used in the file naming for the metric.
        TODO: maybe provide a dictionary with the equivalences instead 
        (this is for the regressions, for which the file name is 
        informative)
    save_files_dir: str
        Path where to store the generated files
    keep_rows_ordered: Boolean (default: True)
        Whether to keep rows ordered as provided in row_names
        If False, orders alphabetically
    keep_cols_ordered: Boolean (default: True)
        Whether to keep columns ordered as provided in col_names
        If False, orders alphabetically

    Returns
    -------
    None
    
    
    """

    ## -- MAIN DATAFRAME -- ##
    # pivot and reindex so that it contains all col_names and rows_names
    metric_df_p = metric_df.pivot(values = metric_var,
                                  index = rows_var, 
                                  columns = cols_var).reindex(index = rows_names,
                                                              columns = cols_names)
    # fill NaNs with the mean of each row (gene)
    # metric_df_p = metric_df_p.apply(lambda row: row.fillna(row.mean()), axis = 1)

    # reorder alphabetically if provided ordered is not kept
    if not keep_rows_ordered:
        metric_df_p = metric_df_p.sort_index(axis = 0)
    if not keep_cols_ordered: 
        metric_df_p = metric_df_p.sort_index(axis = 1)

    ## -- TOTAL COLUMNS DATAFRAME -- ##
    # if sum, mean or median, calculate from the pivoted df
    if total_cols_by == "sum":
        metric_cols_total_df = metric_df_p.sum(axis = 0, skipna = True).to_frame(metric_var) #skipna=True to avoid getting NA as the total when there are NAs in the df
    elif total_cols_by == "mean":
        metric_cols_total_df = metric_df_p.mean(axis = 0, skipna = True).to_frame(metric_var)
    elif total_cols_by == "median":
        metric_cols_total_df = metric_df_p.median(axis = 0, skipna = True).to_frame(metric_var)
    # otherwise, get from metric_df
    else:
        metric_cols_total_df = metric_df.loc[(metric_df[rows_var] == total_cols_by)
                                            & (metric_df[cols_var].isin(cols_names))][[cols_var, metric_var]].set_index(
                                            cols_var).reindex(index = cols_names)
        ## reorder alphabetically if provided ordered is not kept
        if not keep_cols_ordered:
            metric_cols_total_df = metric_cols_total_df.sort_index(axis = 0)
    
    ## -- TOTAL ROWS DATAFRAME -- ##
    # if sum, mean or median, calculate from the pivoted df
    if total_rows_by == "sum":
        metric_rows_total_df = metric_df_p.sum(axis = 1, skipna = True).to_frame(metric_var)
    elif total_rows_by == "mean":
        metric_rows_total_df = metric_df_p.mean(axis = 1, skipna = True).to_frame(metric_var)
    elif total_rows_by == "median":
        metric_rows_total_df = metric_df_p.median(axis = 1, skipna = True).to_frame(metric_var)
    # otherwise, get from metric_df
    else:
        metric_rows_total_df = metric_df.loc[(metric_df[cols_var] == total_rows_by)
                                            & (metric_df[rows_var].isin(rows_names))][[rows_var, metric_var]].set_index(
                                            rows_var).reindex(index = rows_names)
        ## reorder alphabetically if provided ordered is not kept
        if not keep_rows_ordered:
            metric_rows_total_df = metric_rows_total_df.sort_index(axis = 0)

    ## -- SAVE OR RETURN -- ##
    metric_df_p.to_csv(os.path.join(save_files_dir, f"{metric_var4file.lower()}.tsv"), sep = "\t")
    display(metric_df_p)
    print( metric_df_p.shape)
    assert metric_df_p.shape == (len(rows_names), len(cols_names))
    metric_rows_total_df.to_csv(os.path.join(save_files_dir, f"{metric_var4file.lower()}.total_{rows_var.lower()}.tsv"), sep = "\t")
    display(metric_rows_total_df)
    print(metric_rows_total_df.shape)
    assert metric_rows_total_df.shape == (len(rows_names), 1)
    metric_cols_total_df.to_csv(os.path.join(save_files_dir, f"{metric_var4file.lower()}.total_{cols_var.lower()}.tsv"), sep = "\t") # having points here may collapse with the file naming in the main function
    display(metric_cols_total_df)
    print(metric_cols_total_df.shape)
    assert metric_cols_total_df.shape == (len(cols_names), 1)
        
    return None

In [ ]:
def process_mutdensity(mutdensity_file, 
                    rows_names, cols_names, 
                    save_files_dir):
    """
    Generates and saves pivoted dataframes of mutation rates,
    with columns as samples and rows as genes. Does the same with
    a two column table for the total of the genes and the total
    of the samples. Creates as many versions as those specified in 
    metrics, mutdensity_df["REGIONS"] and mutdensity_df["MUTTYPES"]
    
    Parameters
    ----------
    mutdensity_file: str
        Path to the mutation rates file
    rows_names: list
        List of values to be used as the row names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add rows with NA we want to keep for downstream 
        analysis
    cols_names: list
        List of values to be used as the column names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add columns with NA we want to keep for downstream 
        analysis
    save_files_dir: str
        Path where to store the generated files

    Returns
    -------
    None
    """
    
    # load master mutdensity file
    mutdensity_df = pd.read_csv(mutdensity_file, sep = "\t")

    # create tables
    metrics = ["MUTDENSITY_MB", "MUTREADSRATE_MB"] # update when new metrics are available in deepCSA
    for metric_var in metrics:
        for region in mutdensity_df["REGIONS"].unique():
            for muttype in mutdensity_df["MUTTYPES"].unique():
                
                mutdensity_df_f = mutdensity_df.loc[(mutdensity_df["REGIONS"] == region) 
                                            & (mutdensity_df["MUTTYPES"] == muttype)]
                mutdensity_df_f = mutdensity_df_f.rename({"GENE": "gene", "SAMPLE_ID": "sample"}, axis = 1)

                print(f'{metric_var.split("_")[0]}.{"".join(region.split("_"))}_{muttype.lower().replace("_", "")}')
                create_metric_table(metric_df = mutdensity_df_f,
                            metric_var = metric_var,
                            rows_var = "gene", cols_var = "sample",
                            rows_names = rows_names, cols_names = cols_names, 
                            total_cols_by = "ALL_GENES", # not calculated in deepCSA for some alterations
                            total_rows_by = "all_samples",
                            metric_var4file = f'{metric_var.split("_")[0]}.{"".join(region.split("_"))}_{muttype.lower().replace("_", "")}', 
                            save_files_dir = save_files_dir, 
                            keep_rows_ordered = True, keep_cols_ordered = True)

    return None

In [ ]:
process_mutdensity(mutdensity_file, rows_names = panel, 
                cols_names = samples,
                save_files_dir = os.path.join(cluster_dir, "path/to/your/folder"))

MUTRATE.proteinaffecting_alltypes


sample        P19_0047_BDO_01  P19_0009_BTR_01  P19_0008_BDO_01  \
gene                                                              
KMT2D                0.380316         1.580258         2.133347   
ARID1A               1.705234         1.238819         2.961963   
KDM6A                3.233109         0.851105         6.185926   
RBM10                3.653510         1.186349         7.727921   
EP300                0.375534         1.928828         2.377895   
STAG2                2.410264         1.049509         4.226403   
CREBBP               0.290401         3.627967         2.231568   
NOTCH2               0.382225         0.923781         1.718655   
FOXQ1                1.248806         2.747091         9.006124   
CDKN1A               5.479042         1.919438         9.469636   
KMT2C                0.409842         0.776130         1.116205   
TP53                 0.280565         3.567183         2.449108   
RB1                  0.262450         0.854414         0.855110   
FGFR3                0.238426         0.937535         2.443523   
PIK3CA               0.943423         0.000000         0.682079   
TERTpromoter         0.000000        55.547326        21.080147   

sample        P19_0001_BTR_01  P19_0041_BDO_01  P19_0029_BTR_01  \
gene                                                              
KMT2D                0.516037         3.759331         7.447288   
ARID1A               1.425842         0.657147         1.096496   
KDM6A                3.406395         4.374719         6.219180   
RBM10                1.322204         2.311173         1.206744   
EP300                0.201736         1.397164         1.108978   
STAG2                1.878942         1.091604         5.591493   
CREBBP               0.227303         1.023782         0.970520   
NOTCH2               0.133166         1.207118         0.987257   
FOXQ1                0.000000         3.390599        11.373127   
CDKN1A               5.108047         7.183337         3.775483   
KMT2C                0.287293         0.318883         0.295431   
TP53                 0.150192         0.767017         1.303053   
RB1                  0.424987         0.310863         0.105690   
FGFR3                0.000000         0.302286         0.316097   
PIK3CA               0.587002         0.000000         0.000000   
TERTpromoter         0.000000         0.000000       175.231086   

sample        P19_0007_BDO_01  P19_0008_BTR_01  P19_0014_BDO_01  \
gene                                                              
KMT2D                1.160241         2.292995         1.180725   
ARID1A               1.898394         3.348342         1.555621   
KDM6A                3.015262         6.663362         8.395906   
RBM10                7.389589         5.715656         5.237042   
EP300                0.968829         1.956644         0.977304   
STAG2                0.557843         4.533050         2.299578   
CREBBP               0.604585         1.888836         1.414535   
NOTCH2               1.036517         1.448156         0.672143   
FOXQ1                4.782862         6.666972         8.490444   
CDKN1A               1.714181         7.697034        15.216838   
KMT2C                0.278816         1.153420         0.785264   
TP53                 1.593400         2.250836         1.238217   
RB1                  0.482935         0.647438         0.552607   
FGFR3                0.000000         0.930157         0.295416   
PIK3CA               0.960407         0.000000         0.502552   
TERTpromoter        43.402778        12.205467         0.000000   

sample        P19_0005_BDO_01  P19_0018_BTR_01  P19_0027_BTR_01  \
gene                                                              
KMT2D                0.777456         3.903164         0.177333   
ARID1A               0.876580         1.047720         0.243674   
KDM6A                5.781105         4.796721         0.145748   
RBM10                5.918432         4.9333

(16, 79)


MUTRATE_MB
gene                    
KMT2D           2.291866
ARID1A          2.051112
KDM6A           4.548288
RBM10           4.819402
EP300           1.128414
STAG2           2.141046
CREBBP          1.058169
NOTCH2          0.916899
FOXQ1           5.160700
CDKN1A          5.960047
KMT2C           0.567687
TP53            1.344887
RB1             0.380435
FGFR3           0.442098
PIK3CA          0.874151
TERTpromoter   19.017392

(16, 1)


...

(16, 79)


MUTREADSRATE_MB
gene                         
KMT2D                     0.0
ARID1A                    0.0
KDM6A                     0.0
RBM10                     0.0
EP300                     0.0
STAG2                     0.0
CREBBP                    0.0
NOTCH2                    0.0
FOXQ1                     0.0
CDKN1A                    0.0
KMT2C                     0.0
TP53                      0.0
RB1                       0.0
FGFR3                     0.0
PIK3CA                    0.0
TERTpromoter              0.0

(16, 1)


MUTREADSRATE_MB
sample                          
P19_0047_BDO_01              0.0
P19_0009_BTR_01              0.0
P19_0008_BDO_01              0.0
P19_0001_BTR_01              0.0
P19_0041_BDO_01              0.0
...                          ...
P19_0051_BTR_01              0.0
P19_0052_BDO_01              0.0
P19_0052_BTR_01              0.0
P19_0053_BDO_01              0.0
P19_0053_BTR_01              0.0

[79 rows x 1 columns]

(79, 1)


In [21]:
def process_oncodrivefml(oncodrivefml_dir, total_cols_by,
                         rows_names, cols_names, 
                         save_files_dir):
    """
    Generates and saves pivoted dataframes of OncodriveFML metrics
    (z-score and difference between observed and expected mean 
    deleteriousness scores), with columns as samples and rows as genes.
    Does the same with a two column table for the total of
    the genes and the total of the samples.
    Creates as many versions as those specified in 
    metrics and muts4profile, and for each type created a version with all
    values and another with significant values only
    
    Parameters
    ----------
    oncodrivefml_dir: str
        Path to the directory where the output files of OncodriveFML
        are stored
    total_cols_by: str
        How to calculate the total for the columns of the dataframe.
        Can be "sum", "mean" or "median"
    rows_names: list
        List of values to be used as the row names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add rows with NA we want to keep for downstream 
        analysis
    cols_names: list
        List of values to be used as the column names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add columns with NA we want to keep for downstream 
        analysis
    save_files_dir: str
        Path where to store the generated files

    Returns
    -------
    None
    """

    # load OncodriveFML results in a df
    oncodrivefml_df = pd.DataFrame()
    for file in os.listdir(oncodrivefml_dir):
        sample_df = pd.read_csv(f"{oncodrivefml_dir}/{file}/{file.split('.')[0]}-oncodrivefml.tsv.gz", 
                                sep = "\t", header = 0)
        sample_df["sample"] = file
        oncodrivefml_df = pd.concat((oncodrivefml_df, sample_df)).reset_index(drop = True)

    # compute new metric: difference between expected and observed mean deleteriousness scores
    oncodrivefml_df["DIFF-OBSvsEXP"] = oncodrivefml_df["AVG_SCORE_OBS"] - oncodrivefml_df["POPULATION_MEAN"]

    # create tables
    metrics = ["Z-SCORE", "DIFF-OBSvsEXP"]
    # muts4profile = [".all", ".non_prot_aff"] # muts used to create the bg profile
    muts4profile = [".all"] # muts used to create the bg profile # Ferriol deactivated nonprotaff profile in the latest run

    for metric_var in metrics:
        for profile in muts4profile:
            
            oncodrivefml_df_f = oncodrivefml_df.loc[oncodrivefml_df["sample"].str.contains(profile)]
            oncodrivefml_df_f["sample"] = oncodrivefml_df_f.apply(
                lambda row: row["sample"].split(".")[0], axis = 1)    # after use, remove profile info to every sample id
            oncodrivefml_df_f = oncodrivefml_df_f.rename({"GENE_ID": "gene"}, axis = 1)

            ## all oncodrivefml values, regardless of significance
            print(metric_var, profile)
            create_metric_table(metric_df = oncodrivefml_df_f,
                            metric_var = metric_var,
                            rows_var = "gene", cols_var = "sample",
                            rows_names = rows_names, cols_names = cols_names, 
                            total_cols_by = total_cols_by,
                            total_rows_by = "all_samples",
                            metric_var4file = f'oncodrivefml.{"".join(metric_var.split("-"))}_{"".join(profile[1:].split("_"))}prof_nosignificant', 
                            save_files_dir = save_files_dir, 
                            keep_rows_ordered = True, keep_cols_ordered = True)

            ## only significant oncodrivefml values (qvalue is not calculated for one sample only)
            ### aproach 1: filter out non-significant values, generates NA
            # oncodrivefml_df_f = oncodrivefml_df_f.loc[(oncodrivefml_df_f["Q_VALUE"] < 0.05)  
            #                                           | ((oncodrivefml_df_f["Q_VALUE"].isna()) & (oncodrivefml_df_f["P_VALUE"] < 0.05))]
            ### aproach 2: fill non-significant values with zero (for regressions)
            oncodrivefml_df_f.loc[(oncodrivefml_df_f["Q_VALUE"] > 0.05)  
                                | ((oncodrivefml_df_f["Q_VALUE"].isna()) & (oncodrivefml_df_f["P_VALUE"] > 0.05)), metric_var] = 0
            print(metric_var, profile, "significant")
            create_metric_table(metric_df = oncodrivefml_df_f,
                            metric_var = metric_var,
                            rows_var = "gene", cols_var = "sample",
                            rows_names = rows_names, cols_names = cols_names, 
                            total_cols_by = total_cols_by,
                            total_rows_by = "all_samples",
                            metric_var4file = f'oncodrivefml.{"".join(metric_var.split("-"))}_{"".join(profile[1:].split("_"))}prof_significant', 
                            save_files_dir = save_files_dir, 
                            keep_rows_ordered = True, keep_cols_ordered = True)
            
    return None

In [ ]:
process_oncodrivefml(oncodrivefml_dir, total_cols_by = "mean",
                     rows_names = panel, cols_names = samples,
                     save_files_dir = os.path.join(cluster_dir, "path/to/your/folder"))

Z-SCORE .all


sample        P19_0047_BDO_01  P19_0009_BTR_01  P19_0008_BDO_01  \
gene                                                              
KMT2D                 4.99217          7.01956          5.44918   
ARID1A                9.62117          1.40433          2.87406   
KDM6A                 6.69819          0.75526          5.92705   
RBM10                 6.09922          2.04136          6.53346   
EP300                -0.02613          4.70254          6.01223   
STAG2                 6.50304         -0.44125          3.98583   
CREBBP               -1.32605          7.23774          2.58253   
NOTCH2                0.51628         -0.50866          2.26064   
FOXQ1                 1.38461          1.08873          1.88897   
CDKN1A                2.87963          3.06420          1.31101   
KMT2C                 0.93560         -0.09297          0.65092   
TP53                  1.71560          4.60993          1.25920   
RB1                   0.50353          2.06991         -0.45114   
FGFR3                -0.65195          0.26518          0.65377   
PIK3CA                0.06542              NaN         -0.23822   
TERTpromoter              NaN          1.43672          0.17869   

sample        P19_0001_BTR_01  P19_0041_BDO_01  P19_0029_BTR_01  \
gene                                                              
KMT2D                 6.13009         19.03029         30.60342   
ARID1A                7.37754          2.97847          2.10829   
KDM6A                 5.80870          7.80959          8.11022   
RBM10                 3.31119          4.95277          1.44402   
EP300                 0.22702          4.57096          2.92526   
STAG2                 5.42368          1.94336          5.29951   
CREBBP                0.33684          2.80056          2.21936   
NOTCH2                1.14850          4.00016          2.48911   
FOXQ1                -0.49169          2.03696          1.73969   
CDKN1A                1.80367          1.38145          2.89865   
KMT2C                 1.13325          0.25168         -0.71330   
TP53                      NaN         -0.22901          1.99520   
RB1                   0.73875         -0.02617          0.36633   
FGFR3                -0.59296          0.74948         -0.80407   
PIK3CA               -0.05401              NaN              NaN   
TERTpromoter              NaN         -0.68162          0.84682   

sample        P19_0007_BDO_01  P19_0008_BTR_01  P19_0014_BDO_01  \
gene                                                              
KMT2D                 6.86394          7.62778          7.87785   
ARID1A                6.81528          7.35166          6.28973   
KDM6A                 3.87254          5.74533         10.73577   
RBM10                 8.34870          6.78474          6.22536   
EP300                 3.96738          4.84700          2.78091   
STAG2                -0.03334          6.69734          4.04976   
CREBBP                0.40924          2.38557          2.64619   
NOTCH2                2.52552          2.32106          0.91904   
FOXQ1                -0.41205          0.79936          1.24271   
CDKN1A                0.68673          1.87609          3.98252   
KMT2C                 1.65833          0.87715          2.18872   
TP53                  1.79182          2.25684          3.14256   
RB1                   0.69155          0.74161         -0.00390   
FGFR3                     NaN         -0.46595         -0.26727   
PIK3CA                0.55418              NaN         -0.71991   
TERTpromoter          0.14587          0.98742         -0.79939   

sample        P19_0005_BDO_01  P19_0018_BTR_01  P19_0027_BTR_01  \
gene                                                              
KMT2D                 5.44145         21.74145         -2.51972   
ARID1A                1.31713          3.22726         -2.22486   
KDM6A                11.57694          6.80592         -0.40959   
RBM10                 9.73146          6.788

(16, 79)


Z-SCORE
gene                   
KMT2D         116.91111
ARID1A         56.41793
KDM6A          59.57240
RBM10          62.26885
EP300          27.27174
STAG2          33.73839
CREBBP         19.26229
NOTCH2         21.78539
FOXQ1          14.25517
CDKN1A         17.20629
KMT2C           8.85581
TP53           17.78687
RB1             3.85516
FGFR3          -2.34196
PIK3CA         -0.04205
TERTpromoter    2.33466

(16, 1)


...

(16, 79)


DIFF-OBSvsEXP
gene                       
KMT2D             10.666520
ARID1A             8.763081
KDM6A              9.746126
RBM10             10.714135
EP300              4.964920
STAG2              7.176908
CREBBP             4.066864
NOTCH2             4.735023
FOXQ1              5.105091
CDKN1A             7.986317
KMT2C              3.001376
TP53               6.957438
RB1                1.948081
FGFR3              0.000000
PIK3CA             0.000000
TERTpromoter       0.967690

(16, 1)


DIFF-OBSvsEXP
sample                        
P19_0047_BDO_01       4.856457
P19_0009_BTR_01       2.817470
P19_0008_BDO_01       3.062155
P19_0001_BTR_01       4.750193
P19_0041_BDO_01       5.429536
...                        ...
P19_0051_BTR_01       6.273643
P19_0052_BDO_01       4.047876
P19_0052_BTR_01       6.285014
P19_0053_BDO_01       4.574419
P19_0053_BTR_01       3.529281

[79 rows x 1 columns]

(79, 1)


In [23]:
def process_omega_mle(omega_dir,
                      total_cols_by,
                      rows_names, cols_names, 
                      save_files_dir,
                      omega_modality = "mle"):
    """
    Generates and saves pivoted dataframes of omega (MLE or bayes),
    with columns as samples and rows as genes.
    Does the same with a two column table for the total of
    the genes and the total of the samples.
    Creates as many versions as those specified in 
    metrics and muts4profile, and for each type created a version with all
    values and another with significant values only

    Parameters
    ----------
    omega_dir: str
        Path to the directory where the output files of omega
        are stored
    total_cols_by: str
        How to calculate the total for the columns of the dataframe.
        Can be "sum", "mean" or "median"
    rows_names: list
        List of values to be used as the row names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add rows with NA we want to keep for downstream 
        analysis
    cols_names: list
        List of values to be used as the column names of the 
        pivoted dataframe. Used both to subset the df if needed
        and to add columns with NA we want to keep for downstream 
        analysis
    save_files_dir: str
        Path where to store the generated files
    omega_modality: str (default: "mle")
        Omega modality used to compute omegas. Can be "mle" or "bayes".

    Returns
    -------
    None
    """

    # load omega results in a df
    omega_df = pd.DataFrame()
    files = [file for file in os.listdir(omega_dir) if omega_modality in file]  
    for file in files:
        sample_df = pd.read_csv(f"{omega_dir}/{file}", sep = "\t", header = 0)
        sample_df["sample"] = file
        omega_df = pd.concat((omega_df, sample_df)).reset_index(drop = True)

    # create tables
    metric_var = "dnds"
    impacts4muts = omega_df["impact"].unique() # mutation impact filter used to compute the omega values
    print(impacts4muts)
    # muts4profile = ["NoValue", "non_prot_aff"] # muts used to create the bg profile
    muts4profile = ["NoValue"] # muts used to create the bg profile # Ferriol deactivated nonprotaff profile in the latest run
    # uniqueormulti_muts = ["NoValue", "multi"] # whether each mutation is considered once or as many ALT reads is has
    uniqueormulti_muts = ["NoValue"]

    ## equivalence for file names needed for the regression module
    names4files_profile = {
        "NoValue": "allprof",
        "non_prot_aff": "nonprotaffprof"
    }
    names4files_uniqmultimuts = {
        "NoValue": "uniquemuts",
        "multi": "multimuts"
    }

    samples = list(set([".".join(file.split(".")[:2]) for file in omega_df["sample"]]))
    # print(samples)
    for profile in muts4profile:
        for uniqormulti in uniqueormulti_muts:
            # analysis_info = [f'{sampl}.{profile}.{uniqormulti}.tsv'.replace('.NoValue', '') for sampl in samples] # this way we do the subset properly (checked)
            analysis_info = [f'{sampl}.{profile}.{uniqormulti}.global_loc.tsv'.replace('.NoValue', '') for sampl in samples] # this way we do the subset properly (checked)
            # print(analysis_info)
            for impact in impacts4muts:
                # print(impact)
                print(impact, profile, uniqormulti)
                if impact in ['essential_splice_plus', 'truncating_plus']:
                    continue
                omega_df_f = omega_df.loc[(omega_df["sample"].isin(analysis_info)) &
                                            (omega_df["impact"] == impact)]
                # display(omega_df_f)
                omega_df_f["sample"] = omega_df_f.apply(lambda row: row["sample"].split(".")[1], axis = 1)   # after use, remove analysis info to every sample id
                omega_df_f = omega_df_f.rename({"GENE_ID": "gene"}, axis = 1)

                ## all omega values, regardless of significance
                
                metric_var4file = f"omega.{metric_var}_{omega_modality}_{impact.replace('_', '')}_{names4files_profile[profile]}_{names4files_uniqmultimuts[uniqormulti]}_nosignificant"
                create_metric_table(metric_df = omega_df_f,
                                    metric_var = metric_var,
                                    rows_var = "gene", cols_var = "sample",
                                    rows_names = rows_names, cols_names = cols_names, 
                                    total_cols_by = total_cols_by,
                                    total_rows_by = "all_samples",
                                    metric_var4file = metric_var4file, 
                                    save_files_dir = save_files_dir, 
                                    keep_rows_ordered = True, keep_cols_ordered = True)
                
                ## only significant omega values
                print(impact, profile, uniqormulti, "significant")
                metric_var4file = f"omega.{metric_var}_{omega_modality}_{impact.replace('_', '')}_{names4files_profile[profile]}_{names4files_uniqmultimuts[uniqormulti]}_significant"
                ### aproach 1: filter out non-significant values, generates NA
                omega_df_f = omega_df_f.loc[(omega_df_f["pvalue"] < 0.05)]
                ### aproach 2: fill non-significant values with zero (for regressions)
                # omega_df_f.loc[(omega_df_f["pvalue"] > 0.05), metric_var] = 0
                create_metric_table(metric_df = omega_df_f,
                                    metric_var = metric_var,
                                    rows_var = "gene", cols_var = "sample",
                                    rows_names = rows_names, cols_names = cols_names, 
                                    total_cols_by = total_cols_by,
                                    total_rows_by = "all_samples",
                                    metric_var4file = metric_var4file, 
                                    save_files_dir = save_files_dir, 
                                    keep_rows_ordered = True, keep_cols_ordered = True)
                

    return None

In [ ]:
process_omega_mle(omega_dir, total_cols_by = "mean", 
                  rows_names = panel, cols_names = samples,
                  save_files_dir = os.path.join(cluster_dir, "path/to/your/folder"))

['missense' 'nonsynonymous_splice' 'splice_region_variant'
 'essential_splice_plus' 'truncating_plus' 'nonsense' 'truncating'
 'essential_splice']
missense NoValue NoValue


/tmp/ipykernel_3351310/2542403141.py:85: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  omega_df_f["sample"] = omega_df_f.apply(lambda row: row["sample"].split(".")[1], axis = 1)   # after use, remove analysis info to every sample id


sample        P19_0047_BDO_01  P19_0009_BTR_01  P19_0008_BDO_01  \
gene                                                              
KMT2D                0.841406         1.327734         1.197754   
ARID1A               2.031641         1.673438         1.370313   
KDM6A                4.214063         1.750000         3.209375   
RBM10                3.343945         1.593750         2.244531   
EP300                1.784375         2.925000         2.250000   
STAG2                3.687500         1.065820         1.537500   
CREBBP               1.203125         4.181250         2.312891   
NOTCH2               1.821875         2.200000         1.953906   
FOXQ1                1.937402         0.899609         1.025806   
CDKN1A               3.460938         1.639844         1.457031   
KMT2C                1.957080         1.951660         1.308203   
TP53                 2.575000         8.175000         3.591406   
RB1                  2.925195         2.930859         2.281250   
FGFR3                     NaN         1.042578         1.976514   
PIK3CA               6.065628              NaN         1.075732   
TERTpromoter              NaN       103.325000        27.478125   

sample        P19_0001_BTR_01  P19_0041_BDO_01  P19_0029_BTR_01  \
gene                                                              
KMT2D                2.075391         2.303125         3.706348   
ARID1A               2.009570         1.172076         1.506256   
KDM6A                6.112497         4.061719         3.835950   
RBM10                2.268750         2.611719         1.421680   
EP300                2.502734         3.240625         3.176563   
STAG2                6.556250         2.115576         4.075098   
CREBBP               1.753125         3.659375         2.455469   
NOTCH2               1.212890         4.723438         2.487500   
FOXQ1                     NaN         0.898047         4.862500   
CDKN1A               2.873633         1.503125         0.946877   
KMT2C                2.146863         0.956250         1.103320   
TP53                      NaN         5.121875         5.968762   
RB1                  7.087500         0.806445         0.841992   
FGFR3                     NaN         1.217163         0.475293   
PIK3CA               8.087500              NaN              NaN   
TERTpromoter              NaN              NaN       545.350000   

sample        P19_0007_BDO_01  P19_0008_BTR_01  P19_0014_BDO_01  \
gene                                                              
KMT2D                1.701563         1.391406         1.209570   
ARID1A               1.576758         1.554688         1.534375   
KDM6A                4.793750         2.576172         5.512500   
RBM10                2.482813         2.062500         3.149219   
EP300                3.415625         2.015820         1.472656   
STAG2                0.611425         1.192188         2.169336   
CREBBP               2.551563         1.778125         2.585938   
NOTCH2               5.659375         1.734375         1.448438   
FOXQ1                3.712500         1.080516         2.588867   
CDKN1A               3.403528         0.669519         3.792188   
KMT2C                0.778124         1.537500         1.202734   
TP53                10.437500         3.406250         2.672070   
RB1                  2.778125         1.222266         1.925049   
FGFR3                     NaN         0.677539         0.665039   
PIK3CA               5.628131              NaN         1.581250   
TERTpromoter       186.500000        15.647656              NaN   

sample        P19_0005_BDO_01  P19_0018_BTR_01  P19_0027_BTR_01  \
gene                                                              
KMT2D                1.054492         3.005469         0.390234   
ARID1A               1.185742         1.286719         0.874219   
KDM6A                3.745313         3.694482         0.999927   
RBM10                2.500781         5.4968

(16, 79)


dnds
gene                   
KMT2D          1.869922
ARID1A         1.533789
KDM6A          4.084375
RBM10          3.313281
EP300          3.006247
STAG2          1.768750
CREBBP         2.795313
NOTCH2         2.542188
FOXQ1          2.536377
CDKN1A         2.412500
KMT2C          1.421875
TP53           5.226563
RB1            1.724609
FGFR3          0.884277
PIK3CA         2.873242
TERTpromoter  63.225000

...

(16, 79)


dnds
gene                   
KMT2D         14.850781
ARID1A        12.173242
KDM6A         45.631250
RBM10         35.100000
EP300         12.017310
STAG2         13.811133
CREBBP         8.492188
NOTCH2         5.315625
FOXQ1               NaN
CDKN1A         5.612500
KMT2C          3.334375
TP53           4.883008
RB1            2.674219
FGFR3          0.291553
PIK3CA              NaN
TERTpromoter        NaN

(16, 1)


dnds
sample                    
P19_0047_BDO_01  38.604375
P19_0009_BTR_01  13.098307
P19_0008_BDO_01  10.743205
P19_0001_BTR_01  95.568748
P19_0041_BDO_01  32.050456
...                    ...
P19_0051_BTR_01  49.716357
P19_0052_BDO_01  48.585286
P19_0052_BTR_01  31.771354
P19_0053_BDO_01  22.305073
P19_0053_BTR_01  15.019922

[79 rows x 1 columns]

(79, 1)


In [ ]:
# IMPORTANT: for omega you may not want to run regressions for all impacts  
# you have to subset the files and delete those containing all the genes
# for the all-genes files, we keep them as they are 
# below an example of hot to do this: 
trunc_genes = ['KMT2D','ARID1A','KDM6A','RBM10','EP300','STAG2',
            'CREBBP','NOTCH2','CDKN1A','KMT2C'] 
print(len(trunc_genes))
missense_genes = ['KMT2D','KDM6A','RBM10','EP300','STAG2',
                'CREBBP','NOTCH2','TP53', 'RB1', 'FOXQ1',
                'ARID1A', 'CDKN1A', "KMT2C"] 
print(len(missense_genes))


omega_trunc = pd.read_csv(os.path.join(cluster_dir, "path/to/your/folder",
                                    "omega.dnds_mle_truncating_allprof_uniquemuts_nosignificant.tsv"),
                        sep = "\t")
omega_trunc = omega_trunc.loc[omega_trunc["gene"].isin(trunc_genes)]
omega_trunc.to_csv(os.path.join(cluster_dir, "path/to/your/folder",
                                "omega.dnds_mle_truncating_allprof_uniquemuts_nosignificant.truncantinggenes.tsv"),
                sep = "\t", index = False)
os.remove(os.path.join(cluster_dir, "path/to/your/folder",
                                    "omega.dnds_mle_truncating_allprof_uniquemuts_nosignificant.tsv"))
display(omega_trunc)

omega_missense = pd.read_csv(os.path.join(cluster_dir, "path/to/your/folder", 
                                        "omega.dnds_mle_missense_allprof_uniquemuts_nosignificant.tsv"),
                    sep = "\t")
omega_missense = omega_missense.loc[omega_missense["gene"].isin(missense_genes)]
omega_missense.to_csv(os.path.join(cluster_dir, "path/to/your/folder",
                                "/omega.dnds_mle_missense_allprof_uniquemuts_nosignificant.missensegenes.tsv"),
                sep = "\t", index = False)
os.remove(os.path.join(cluster_dir, "path/to/your/folder", 
                                        "omega.dnds_mle_missense_allprof_uniquemuts_nosignificant.tsv"))
display(omega_missense)

10
13


gene  P19_0047_BDO_01  P19_0009_BTR_01  P19_0008_BDO_01  \
0    KMT2D         6.385938         7.100195         5.274951   
1   ARID1A        37.150000         2.929297         6.564856   
2    KDM6A        72.906250              NaN        19.831250   
3    RBM10        50.925000         1.925098        20.250000   
4    EP300         3.553174        10.918726         8.925195   
5    STAG2        43.137488         4.220311        10.703125   
6   CREBBP         2.426613        16.337891         2.675000   
7   NOTCH2         2.079675              NaN         2.762305   
9   CDKN1A        20.706250         5.948242         9.125769   
10   KMT2C         2.188281              NaN         2.371875   

    P19_0001_BTR_01  P19_0041_BDO_01  P19_0029_BTR_01  P19_0007_BDO_01  \
0         13.981055        51.725000        69.100000        14.173438   
1         49.037451         5.248413         3.652734        31.250000   
2        121.237500        56.025000        52.673438        47.225000   
3         36.393750        29.887500         5.946875       127.300000   
4               NaN        18.524805         4.344092        13.326559   
5         57.949902         7.325098        42.198438         4.525000   
6               NaN         2.462500         4.093799              NaN   
7               NaN         5.887701         5.718750         3.310938   
9         37.762451        32.603125        17.462500              NaN   
10         3.442286         2.158789              NaN         6.798450   

    P19_0008_BTR_01  P19_0014_BDO_01  P19_0005_BDO_01  P19_0018_BTR_01  \
0          4.701563         7.029686         6.784766        47.375000   
1          7.932813        10.665625         4.719336         7.109351   
2         19.303125        84.700000        56.811719        52.325391   
3         12.387549        34.487500        63.487500        28.471875   
4          5.796875         6.155469         2.425000         6.406201   
5         19.637500        11.654675        11.599805        34.475000   
6          2.535938         4.643945         4.744531         7.834375   
7          1.826563         2.560937              NaN         4.071875   
9          7.191016        29.575000         6.850488        17.328125   
10         2.121875         4.681250         2.830078         1.358984   

    P19_0027_BTR_01  P19_0029_BDO_01  P19_0045_BTR_01  P19_0007_BTR_01  \
0               NaN        58.648438        55.371875         9.651563   
1               NaN         3.356348        28.756250        18.037494   
2               NaN        41.050000        47.262500        39.096997   
3          3.143750         6.156250        88.900000        64.550000   
4          2.968396         4.732837         8.978125         8.557813   
5          2.706641        37.299219         7.293701        20.698438   
6               NaN         5.275000         5.150012              NaN   
7               NaN         2.922656        25.662512         2.957813   
9               NaN         7.868750        54.224609              NaN   
10              NaN         1.662512              NaN              NaN   

    P19_0030_BTR_01  P19_0026_BDO_01  P19_0019_BTR_01  P19_0036_BTR_01  \
0               NaN        34.650012        40.796875         4.087494   
1               NaN         1.552734         5.336328              NaN   
2          6.981250        29.974802        35.112500              NaN   
3               NaN         9.949219         6.894141              NaN   
4               NaN         6.456250         2.666016              NaN   
5          1.998438        88.650000         8.681445              NaN   
6          2.828125         5.429688         1.904687              NaN   
7               NaN         2.818750         6.825006              NaN   
9               NaN         3.662500              NaN              NaN   
10              NaN         2.125195         1.661132              NaN   

    P19_0005_BTR_01  P19_0015_

gene  P19_0047_BDO_01  P19_0009_BTR_01  P19_0008_BDO_01  \
0    KMT2D         0.841406         1.327734         1.197754   
1   ARID1A         2.031641         1.673438         1.370313   
2    KDM6A         4.214063         1.750000         3.209375   
3    RBM10         3.343945         1.593750         2.244531   
4    EP300         1.784375         2.925000         2.250000   
5    STAG2         3.687500         1.065820         1.537500   
6   CREBBP         1.203125         4.181250         2.312891   
7   NOTCH2         1.821875         2.200000         1.953906   
8    FOXQ1         1.937402         0.899609         1.025806   
9   CDKN1A         3.460938         1.639844         1.457031   
10   KMT2C         1.957080         1.951660         1.308203   
11    TP53         2.575000         8.175000         3.591406   
12     RB1         2.925195         2.930859         2.281250   

    P19_0001_BTR_01  P19_0041_BDO_01  P19_0029_BTR_01  P19_0007_BDO_01  \
0          2.075391         2.303125         3.706348         1.701563   
1          2.009570         1.172076         1.506256         1.576758   
2          6.112497         4.061719         3.835950         4.793750   
3          2.268750         2.611719         1.421680         2.482813   
4          2.502734         3.240625         3.176563         3.415625   
5          6.556250         2.115576         4.075098         0.611425   
6          1.753125         3.659375         2.455469         2.551563   
7          1.212890         4.723438         2.487500         5.659375   
8               NaN         0.898047         4.862500         3.712500   
9          2.873633         1.503125         0.946877         3.403528   
10         2.146863         0.956250         1.103320         0.778124   
11              NaN         5.121875         5.968762        10.437500   
12         7.087500         0.806445         0.841992         2.778125   

    P19_0008_BTR_01  P19_0014_BDO_01  P19_0005_BDO_01  P19_0018_BTR_01  \
0          1.391406         1.209570         1.054492         3.005469   
1          1.554688         1.534375         1.185742         1.286719   
2          2.576172         5.512500         3.745313         3.694482   
3          2.062500         3.149219         2.500781         5.496875   
4          2.015820         1.472656         1.795313         2.905469   
5          1.192188         2.169336         1.562891         2.017090   
6          1.778125         2.585938         1.571875         3.671875   
7          1.734375         1.448438         1.421875         3.581641   
8          1.080516         2.588867         1.320313         5.657806   
9          0.669519         3.792188         7.081250              NaN   
10         1.537500         1.202734         1.459570         1.151172   
11         3.406250         2.672070        18.176563         3.500390   
12         1.222266         1.925049         1.866406         4.346875   

    P19_0027_BTR_01  P19_0029_BDO_01  P19_0045_BTR_01  P19_0007_BTR_01  \
0          0.390234         3.003516         2.452344         1.989063   
1          0.874219         0.825000         1.876556         2.145605   
2          0.999927         2.334767         4.110913         2.945264   
3          0.400830         1.321875         9.375000         3.424951   
4          0.837891         1.414063         4.095313         1.760889   
5          0.352783         1.871485         4.818750         1.209375   
6          0.652930         3.090625         2.292969         1.835888   
7          0.657812         1.513281         4.346875         2.590625   
8          0.831056              NaN              NaN         2.117188   
9               NaN         1.158594        13.447656         2.383789   
10         0.677393         2.185938         2.482031         0.677539   
11         1.884766         7.196875        13.556299         9.037500   
12         1.574609         0.726562         1.812500      

------------------------------------------